In [1]:
# Load packages
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from numpy.linalg import solve
from math import sqrt
import fileinput

In [2]:
# Function to return least squares linear approximation coefficients
def linLSQ(points):
    A = np.array([[p[0],1] for p in points])
    b = np.array([p[1] for p in points])
    ATA = np.matmul(np.transpose(A),A)
    ATb = np.matmul(np.transpose(A),b)
    return solve(ATA,ATb)

# Function to return PCA linear approximation coefficients
#def linPCA(points):
#    points_centered = 

In [3]:
# LSQ for three points
def LSQ3(points):
    a1 = points[0][0]; a2 = points[0][1]
    b1 = points[1][0]; b2 = points[1][1]
    c1 = points[2][0]; c2 = points[2][1]
    x = (2*a1*a2-a2*b1-a1*b2+2*b1*b2-a2*c1-b2*c1-a1*c2-b1*c2+2*c1*c2)/(2*(a1**2-a1*b1+b1**2-a1*c1-b1*c1+c1**2))
    y = (-((a1**2+b1**2+c1**2)*(a2+b2+c2))+(a1+b1+c1)*(a1*a2+b1*b2+c1*c2))/((a1+b1+c1)**2-3*(a1**2+b1**2+c1**2))
    return (x,y)

# PSQ for three points
def PSQ3(points):
    a1 = points[0][0]; a2 = points[0][1]
    b1 = points[1][0]; b2 = points[1][1]
    c1 = points[2][0]; c2 = points[2][1]
    mx = (a1+b1+c1)/3
    my = (a2+b2+c2)/3
    m = -((-a1**2+a2**2+a1*b1-b1**2-a2*b2+b2**2+a1*c1+b1*c1-c1**2-a2*c2-b2*c2+c2**2-sqrt(a1**4+2*a1**2*a2**2+a2**4-2*a1**3*b1-2*a1*a2**2*b1+3*a1**2*b1**2-a2**2*b1**2-2*a1*b1**3+b1**4-2*a1**2*a2*b2-2*a2**3*b2+8*a1*a2*b1*b2-2*a2*b1**2*b2-a1**2*b2**2+3*a2**2*b2**2-2*a1*b1*b2**2+2*b1**2*b2**2-2*a2*b2**3+b2**4-2*a1**3*c1-2*a1*a2**2*c1+4*a2**2*b1*c1-2*b1**3*c1-4*a1*a2*b2*c1-4*a2*b1*b2*c1+4*a1*b2**2*c1-2*b1*b2**2*c1+3*a1**2*c1**2-a2**2*c1**2+3*b1**2*c1**2+4*a2*b2*c1**2-b2**2*c1**2-2*a1*c1**3-2*b1*c1**3+c1**4-2*a1**2*a2*c2-2*a2**3*c2-4*a1*a2*b1*c2+4*a2*b1**2*c2+4*a1**2*b2*c2-4*a1*b1*b2*c2-2*b1**2*b2*c2-2*b2**3*c2+8*a1*a2*c1*c2-4*a2*b1*c1*c2-4*a1*b2*c1*c2+8*b1*b2*c1*c2-2*a2*c1**2*c2-2*b2*c1**2*c2-a1**2*c2**2+3*a2**2*c2**2+4*a1*b1*c2**2-b1**2*c2**2+3*b2**2*c2**2-2*a1*c1*c2**2-2*b1*c1*c2**2+2*c1**2*c2**2-2*a2*c2**3-2*b2*c2**3+c2**4))/(2*a1*a2-a2*b1-a1*b2+2*b1*b2-a2*c1-b2*c1-a1*c2-b1*c2+2*c1*c2))
    return (m,my-mx*m)

In [7]:
linLSQ([[0,0],[1,2],[3,3],[-1,2],[5,4],[6,10]])

array([1.01694915, 1.12711864])

In [30]:
# Load packages
from bokeh.plotting import figure, output_file, show, column, row
from bokeh.models import DataTable, TableColumn, NumberFormatter, PointDrawTool, ColumnDataSource, CustomJS, Text, Rect

output_file("lecture22-3points.html")

p = figure(x_range=(0, 20), y_range=(0, 10), width=500, height=250, tools=[], title='Three point exploration')
p.title.text_font_size = '16pt'
p.background_fill_color = 'lightgrey'

source = ColumnDataSource({'x': [1, 5, 9], 'y': [1, 5, 9], 'color': ['red', 'red', 'red']})

rounded = NumberFormatter(format="0.00", )
columns = [TableColumn(field="x", title="x", formatter=rounded), TableColumn(field="y", title="y", formatter=rounded)]
table = DataTable(source=source, columns=columns, editable=True, height=200)

# Least squares line and connectors
xs = np.linspace(0,20,100)
a,b = LSQ3(np.transpose(np.array([source.data['x'],source.data['y']])))
LSQsource = ColumnDataSource(data = {'x':xs, 'y':[a*x+b for x in xs]})
p.line(x='x', y='y', source=LSQsource, legend_label='Least squares', line_width=4, line_color='blue')

LSQconn = ColumnDataSource(data = {
    'x1':[source.data['x'][0],source.data['x'][0]], 'y1':[source.data['y'][0],source.data['y'][0]], 
    'x2':[source.data['x'][1],source.data['x'][1]], 'y2':[source.data['y'][1],source.data['y'][1]], 
    'x3':[source.data['x'][2],source.data['x'][2]], 'y3':[source.data['y'][2],source.data['y'][2]], 
})
p.line(x='x1', y='y1', source=LSQconn, line_width=4, line_color='blue', line_alpha=.4)
p.line(x='x2', y='y2', source=LSQconn, line_width=4, line_color='blue', line_alpha=.4)
p.line(x='x3', y='y3', source=LSQconn, line_width=4, line_color='blue', line_alpha=.4)

# Principal component (least perpendicular squares) and connectors
xs = np.linspace(0,20,100)
a,b = PSQ3(np.transpose(np.array([source.data['x'],source.data['y']])))
PSQsource = ColumnDataSource(data = {'x':xs, 'y':[a*x+b for x in xs]})
p.line(x='x', y='y', source=PSQsource, legend_label='Principal component', line_width=4, line_color='yellow')

PSQconn = ColumnDataSource(data = {
    'x1':[source.data['x'][0],source.data['x'][0]], 'y1':[source.data['y'][0],source.data['y'][0]], 
    'x2':[source.data['x'][1],source.data['x'][1]], 'y2':[source.data['y'][1],source.data['y'][1]], 
    'x3':[source.data['x'][2],source.data['x'][2]], 'y3':[source.data['y'][2],source.data['y'][2]], 
})
p.line(x='x1', y='y1', source=PSQconn, line_width=4, line_color='yellow', line_alpha=.4)
p.line(x='x2', y='y2', source=PSQconn, line_width=4, line_color='yellow', line_alpha=.4)
p.line(x='x3', y='y3', source=PSQconn, line_width=4, line_color='yellow', line_alpha=.4)

# Red points
renderer = p.scatter(x='x', y='y', source=source, color='color', size=20)

# Angle of intersection
extradata = ColumnDataSource(data = {
    'x':[19.5],
    'y':[.5],
    'text':['Angle of intersection: 0.00\nSum of vertical distances: 0.00\nSum of perpendicular distances: 0.00']
})
glyph = Text(x='x', y='y', text='text', angle=0, text_color='green', text_font_size='18pt', text_align='right')
p.add_glyph(extradata,glyph)

# Update function
callback = CustomJS(args=dict(
    source1=LSQsource, source1c=LSQconn,
    source2=PSQsource, source2c=PSQconn,
    source3=extradata,
    source0=source
        ), code="""
    //const f = cb_obj.data;
    const f = source0.data;
    const a1 = f['x'][0]; const a2 = f['y'][0];
    const b1 = f['x'][1]; const b2 = f['y'][1];
    const c1 = f['x'][2]; const c2 = f['y'][2];
    const mx = (a1+b1+c1)/3;
    const my = (a2+b2+c2)/3;
    
    const data1 = source1.data;
    var a = (2*a1*a2-a2*b1-a1*b2+2*b1*b2-a2*c1-b2*c1-a1*c2-b1*c2+2*c1*c2)/(2*(Math.pow(a1,2)-a1*b1+Math.pow(b1,2)-a1*c1-b1*c1+Math.pow(c1,2)));
    var b = (-((Math.pow(a1,2)+b1**2+Math.pow(c1,2))*(a2+b2+c2))+(a1+b1+c1)*(a1*a2+b1*b2+c1*c2))/(Math.pow(a1+b1+c1,2)-3*(Math.pow(a1,2)+Math.pow(b1,2)+c1**2));
    var y = data1['y'];
    for (let i = 0; i < data1['x'].length; i++) {y[i] = a*data1['x'][i]+b}
    source1.change.emit();
    
    const data1c = source1c.data;
    data1c['x1'] = [a1,a1]; data1c['y1'] = [a2,a*a1+b];
    data1c['x2'] = [b1,b1]; data1c['y2'] = [b2,a*b1+b];
    data1c['x3'] = [c1,c1]; data1c['y3'] = [c2,a*c1+b];
    source1c.change.emit();

    const data2 = source2.data;
    const e1 = 1/6*(Math.pow(a1,2)+Math.pow(a2,2)+Math.pow(b1,2)-a2*b2+Math.pow(b2,2)-b1*c1+Math.pow(c1,2)-a1*(b1+c1)-a2*c2-b2*c2+Math.pow(c2,2)-Math.sqrt(-3*(a2*(b1-c1)+b2*c1-b1*c2+a1*(-b2+c2))**2+(Math.pow(a1,2)+Math.pow(a2,2)+Math.pow(b1,2)+Math.pow(b2,2)-b1*c1+Math.pow(c1,2)-a1*(b1+c1)-b2*c2+Math.pow(c2,2)-a2*(b2+c2))**2));
    const e2 = 1/6*(Math.pow(a1,2)+Math.pow(a2,2)+Math.pow(b1,2)-a2*b2+Math.pow(b2,2)-b1*c1+Math.pow(c1,2)-a1*(b1+c1)-a2*c2-b2*c2+Math.pow(c2,2)+Math.sqrt(-3*(a2*(b1-c1)+b2*c1-b1*c2+a1*(-b2+c2))**2+(Math.pow(a1,2)+Math.pow(a2,2)+Math.pow(b1,2)+Math.pow(b2,2)-b1*c1+Math.pow(c1,2)-a1*(b1+c1)-b2*c2+Math.pow(c2,2)-a2*(b2+c2))**2));
    const m1 = (-Math.pow(a1,2)+Math.pow(a2,2)-Math.pow(b1,2)+Math.pow(b2,2)+b1*c1-Math.pow(c1,2)+a1*(b1+c1)-b2*c2+Math.pow(c2,2)-a2*(b2+c2)+Math.sqrt(Math.pow(a1,4)+Math.pow(a2,4)+Math.pow(b1,4)+2*Math.pow(b1,2)*Math.pow(b2,2)+Math.pow(b2,4)-2*Math.pow(b1,3)*c1-2*b1*Math.pow(b2,2)*c1+3*Math.pow(b1,2)*Math.pow(c1,2)-Math.pow(b2,2)*Math.pow(c1,2)-2*b1*Math.pow(c1,3)+Math.pow(c1,4)-2*Math.pow(a1,3)*(b1+c1)-2*b2*(Math.pow(b1,2)+Math.pow(b2,2)-4*b1*c1+Math.pow(c1,2))*c2-(Math.pow(b1,2)-3*Math.pow(b2,2)+2*b1*c1-2*Math.pow(c1,2))*Math.pow(c2,2)-2*b2*Math.pow(c2,3)+Math.pow(c2,4)-2*Math.pow(a2,3)*(b2+c2)+Math.pow(a1,2)*(2*Math.pow(a2,2)-Math.pow(b2,2)+3*(Math.pow(b1,2)+Math.pow(c1,2))+4*b2*c2-Math.pow(c2,2)-2*a2*(b2+c2))-2*a2*(Math.pow(b2,3)-2*b2*Math.pow(c1,2)+Math.pow(b1,2)*(b2-2*c2)+Math.pow(c1,2)*c2+Math.pow(c2,3)+2*b1*c1*(b2+c2))-2*a1*(Math.pow(b1,3)+b1*Math.pow(b2,2)-2*Math.pow(b2,2)*c1+Math.pow(c1,3)+Math.pow(a2,2)*(b1+c1)+2*b2*(b1+c1)*c2+(-2*b1+c1)*Math.pow(c2,2)+2*a2*(-2*b1*b2+b2*c1+b1*c2-2*c1*c2))-Math.pow(a2,2)*(Math.pow(b1,2)-4*b1*c1+Math.pow(c1,2)-3*(Math.pow(b2,2)+Math.pow(c2,2)))))/(-2*b1*b2+b2*c1+a2*(b1+c1)+b1*c2-2*c1*c2+a1*(-2*a2+b2+c2));
    const m2 = -((Math.pow(a1,2)-Math.pow(a2,2)+Math.pow(b1,2)-Math.pow(b2,2)-b1*c1+Math.pow(c1,2)-a1*(b1+c1)+b2*c2-Math.pow(c2,2)+a2*(b2+c2)+Math.sqrt(Math.pow(a1,4)+Math.pow(a2,4)+Math.pow(b1,4)+2*Math.pow(b1,2)*Math.pow(b2,2)+Math.pow(b2,4)-2*Math.pow(b1,3)*c1-2*b1*Math.pow(b2,2)*c1+3*Math.pow(b1,2)*Math.pow(c1,2)-Math.pow(b2,2)*Math.pow(c1,2)-2*b1*Math.pow(c1,3)+Math.pow(c1,4)-2*Math.pow(a1,3)*(b1+c1)-2*b2*(Math.pow(b1,2)+Math.pow(b2,2)-4*b1*c1+Math.pow(c1,2))*c2-(Math.pow(b1,2)-3*Math.pow(b2,2)+2*b1*c1-2*Math.pow(c1,2))*Math.pow(c2,2)-2*b2*Math.pow(c2,3)+Math.pow(c2,4)-2*Math.pow(a2,3)*(b2+c2)+Math.pow(a1,2)*(2*Math.pow(a2,2)-Math.pow(b2,2)+3*(Math.pow(b1,2)+Math.pow(c1,2))+4*b2*c2-Math.pow(c2,2)-2*a2*(b2+c2))-2*a2*(Math.pow(b2,3)-2*b2*Math.pow(c1,2)+Math.pow(b1,2)*(b2-2*c2)+Math.pow(c1,2)*c2+Math.pow(c2,3)+2*b1*c1*(b2+c2))-2*a1*(Math.pow(b1,3)+b1*Math.pow(b2,2)-2*Math.pow(b2,2)*c1+Math.pow(c1,3)+Math.pow(a2,2)*(b1+c1)+2*b2*(b1+c1)*c2+(-2*b1+c1)*Math.pow(c2,2)+2*a2*(-2*b1*b2+b2*c1+b1*c2-2*c1*c2))-Math.pow(a2,2)*(Math.pow(b1,2)-4*b1*c1+Math.pow(c1,2)-3*(Math.pow(b2,2)+Math.pow(c2,2)))))/(-2*b1*b2+b2*c1+a2*(b1+c1)+b1*c2-2*c1*c2+a1*(-2*a2+b2+c2)));
    var m = 0;
    if (e1 > e2) {m = 1/m1;} else {m = 1/m2;}
    b = my-mx*m;
    y = data2['y'];
    for (let i = 0; i < data2['x'].length; i++) {y[i] = m*data2['x'][i]+b}
    source2.change.emit();

    const data2c = source2c.data;
    data2c['x1'] = [a1,(a1+m*a2-b*m)/(1+m*m)]; data2c['y1'] = [a2,m*(a1+m*a2-b*m)/(1+m*m)+b];
    data2c['x2'] = [b1,(b1+m*b2-b*m)/(1+m*m)]; data2c['y2'] = [b2,m*(b1+m*b2-b*m)/(1+m*m)+b];
    data2c['x3'] = [c1,(c1+m*c2-b*m)/(1+m*m)]; data2c['y3'] = [c2,m*(c1+m*c2-b*m)/(1+m*m)+b];
    source2c.change.emit();
    
    const data3 = source3.data;
    const angle = (180*Math.abs(Math.atan(m)-Math.atan(a))/(Math.PI)).toFixed(2);
    const text1 = ['Angle of intersection: ', angle.toString()].join('');
    const hyp1 = Math.hypot(data1c['x1'][0] - data1c['x1'][1], data1c['y1'][0] - data1c['y1'][1]);
    const hyp2 = Math.hypot(data1c['x2'][0] - data1c['x2'][1], data1c['y2'][0] - data1c['y2'][1]);
    const hyp3 = Math.hypot(data1c['x3'][0] - data1c['x3'][1], data1c['y3'][0] - data1c['y3'][1]);
    const text2 = ['Sum of vertical distances: ', ((hyp1+hyp2+hyp3).toFixed(2)).toString()].join('');
    const hypP1 = Math.hypot(data2c['x1'][0] - data2c['x1'][1], data2c['y1'][0] - data2c['y1'][1]);
    const hypP2 = Math.hypot(data2c['x2'][0] - data2c['x2'][1], data2c['y2'][0] - data2c['y2'][1]);
    const hypP3 = Math.hypot(data2c['x3'][0] - data2c['x3'][1], data2c['y3'][0] - data2c['y3'][1]);
    const text3 = ['Sum of perpendicular distances: ', ((hypP1+hypP2+hypP3).toFixed(2)).toString()].join('');
    data3['text'][0] = [text1, text2, text3].join('\\n');
    source3.change.emit();

""")

source.js_on_change('data', callback)
p.js_on_event('mousemove', callback)


draw_tool = PointDrawTool(renderers=[renderer], empty_value='red', num_objects=3)
p.add_tools(draw_tool)
p.toolbar.active_tap = draw_tool

show(column(p, table, sizing_mode="scale_width"))

for line in fileinput.input("lecture22-3points.html", inplace = 1): 
      print(line.replace("  <body>\n", "  <body style=\"margin:5%\">\n"), end='')


In [31]:
# Load packages
from bokeh.plotting import figure, output_file, show, column
from bokeh.models import DataTable, TableColumn, NumberFormatter, PointDrawTool, ColumnDataSource, CustomJS

output_file("lecture22-4points.html")

p = figure(x_range=(0, 20), y_range=(0, 10), width=500, height=250, tools=[], title='Four point exploration')
p.title.text_font_size = '16pt'
p.background_fill_color = 'lightgrey'

source = ColumnDataSource({'x': [1, 3, 5, 9], 'y': [1, 3, 5, 9], 'color': ['red', 'red', 'red', 'red']})

rounded = NumberFormatter(format="0.00", )
columns = [TableColumn(field="x", title="x", formatter=rounded), TableColumn(field="y", title="y", formatter=rounded)]
table = DataTable(source=source, columns=columns, editable=True, width=100)

# Least squares line and connectors
xs = np.linspace(0,20,100)
a,b = LSQ3(np.transpose(np.array([source.data['x'],source.data['y']])))
LSQsource = ColumnDataSource(data = {'x':xs, 'y':[a*x+b for x in xs]})
p.line(x='x', y='y', source=LSQsource, legend_label='Least squares', line_width=4, line_color='blue')

LSQconn = ColumnDataSource(data = {
    'x1':[source.data['x'][0],source.data['x'][0]], 'y1':[source.data['y'][0],source.data['y'][0]], 
    'x2':[source.data['x'][1],source.data['x'][1]], 'y2':[source.data['y'][1],source.data['y'][1]], 
    'x3':[source.data['x'][2],source.data['x'][2]], 'y3':[source.data['y'][2],source.data['y'][2]], 
    'x4':[source.data['x'][3],source.data['x'][3]], 'y4':[source.data['y'][3],source.data['y'][3]], 
})
p.line(x='x1', y='y1', source=LSQconn, line_width=4, line_color='blue', line_alpha=.4)
p.line(x='x2', y='y2', source=LSQconn, line_width=4, line_color='blue', line_alpha=.4)
p.line(x='x3', y='y3', source=LSQconn, line_width=4, line_color='blue', line_alpha=.4)
p.line(x='x4', y='y4', source=LSQconn, line_width=4, line_color='blue', line_alpha=.4)

# Principal component (least perpendicular squares) and connectors
xs = np.linspace(0,20,100)
a,b = PSQ3(np.transpose(np.array([source.data['x'],source.data['y']])))
PSQsource = ColumnDataSource(data = {'x':xs, 'y':[a*x+b for x in xs]})
p.line(x='x', y='y', source=PSQsource, legend_label='Principal component', line_width=4, line_color='yellow')

PSQconn = ColumnDataSource(data = {
    'x1':[source.data['x'][0],source.data['x'][0]], 'y1':[source.data['y'][0],source.data['y'][0]], 
    'x2':[source.data['x'][1],source.data['x'][1]], 'y2':[source.data['y'][1],source.data['y'][1]], 
    'x3':[source.data['x'][2],source.data['x'][2]], 'y3':[source.data['y'][2],source.data['y'][2]], 
    'x4':[source.data['x'][3],source.data['x'][3]], 'y4':[source.data['y'][3],source.data['y'][3]], 
})
p.line(x='x1', y='y1', source=PSQconn, line_width=4, line_color='yellow', line_alpha=.4)
p.line(x='x2', y='y2', source=PSQconn, line_width=4, line_color='yellow', line_alpha=.4)
p.line(x='x3', y='y3', source=PSQconn, line_width=4, line_color='yellow', line_alpha=.4)
p.line(x='x4', y='y4', source=PSQconn, line_width=4, line_color='yellow', line_alpha=.4)

# Red points
renderer = p.scatter(x='x', y='y', source=source, color='color', size=20)

# Angle of intersection
extradata = ColumnDataSource(data = {
    'x':[19.5],
    'y':[.5],
    'text':['Angle of intersection: 0.00\nSum of vertical distances: 0.00\nSum of perpendicular distances: 0.00']
})
glyph = Text(x='x', y='y', text='text', angle=0, text_color='green', text_font_size='18pt', text_align='right')
p.add_glyph(extradata,glyph)

# Update function
callback = CustomJS(args=dict(
    source1=LSQsource, source1c=LSQconn,
    source2=PSQsource, source2c=PSQconn,
    source3=extradata,
    source0=source
        ), code="""
    //const f = cb_obj.data;
    const f = source0.data;
    const a1 = f['x'][0]; const a2 = f['y'][0];
    const b1 = f['x'][1]; const b2 = f['y'][1];
    const c1 = f['x'][2]; const c2 = f['y'][2];
    const d1 = f['x'][3]; const d2 = f['y'][3];
    const mx = (a1+b1+c1+d1)/4;
    const my = (a2+b2+c2+d2)/4;
    
    const data1 = source1.data;
    var a = (3*a1*a2-a2*b1-a1*b2+3*b1*b2-a2*c1-b2*c1-a1*c2-b1*c2+3*c1*c2-a2*d1-b2*d1-c2*d1-a1*d2-b1*d2-c1*d2+3*d1*d2)/(3*Math.pow(a1,2)-2*a1*b1+3*Math.pow(b1,2)-2*a1*c1-2*b1*c1+3*Math.pow(c1,2)-2*a1*d1-2*b1*d1-2*c1*d1+3*Math.pow(d1,2));
    var b = (-((Math.pow(a1,2)+Math.pow(b1,2)+Math.pow(c1,2)+Math.pow(d1,2))*(a2+b2+c2+d2))+(a1+b1+c1+d1)*(a1*a2+b1*b2+c1*c2+d1*d2))/((a1+b1+c1+d1)**2-4*(Math.pow(a1,2)+Math.pow(b1,2)+Math.pow(c1,2)+Math.pow(d1,2)));
    var y = data1['y'];
    for (let i = 0; i < data1['x'].length; i++) {y[i] = a*data1['x'][i]+b}
    source1.change.emit();
    
    const data1c = source1c.data;
    data1c['x1'] = [a1,a1]; data1c['y1'] = [a2,a*a1+b];
    data1c['x2'] = [b1,b1]; data1c['y2'] = [b2,a*b1+b];
    data1c['x3'] = [c1,c1]; data1c['y3'] = [c2,a*c1+b];
    data1c['x4'] = [d1,d1]; data1c['y4'] = [d2,a*d1+b];
    source1c.change.emit();

    const data2 = source2.data;
    const e1 = 1/24*(3*Math.pow(a1,2)+3*Math.pow(a2,2)+3*Math.pow(b1,2)-2*a2*b2+3*Math.pow(b2,2)-2*b1*c1+3*Math.pow(c1,2)-2*a2*c2-2*b2*c2+3*Math.pow(c2,2)-2*b1*d1-2*c1*d1+3*Math.pow(d1,2)-2*a1*(b1+c1+d1)-2*a2*d2-2*b2*d2-2*c2*d2+3*Math.pow(d2,2)-Math.sqrt((3*Math.pow(a1,2)+3*Math.pow(a2,2)+3*Math.pow(b1,2)+3*Math.pow(b2,2)-2*b1*c1+3*Math.pow(c1,2)-2*b2*c2+3*Math.pow(c2,2)-2*(b1+c1)*d1+3*Math.pow(d1,2)-2*a1*(b1+c1+d1)-2*(b2+c2)*d2+3*Math.pow(d2,2)-2*a2*(b2+c2+d2))**2-32*(Math.pow(b2,2)*Math.pow(c1,2)-2*b1*b2*c1*c2+Math.pow(b1,2)*Math.pow(c2,2)-Math.pow(b2,2)*c1*d1+b1*b2*c2*d1+b2*c1*c2*d1-b1*Math.pow(c2,2)*d1+Math.pow(b2,2)*Math.pow(d1,2)-b2*c2*Math.pow(d1,2)+Math.pow(c2,2)*Math.pow(d1,2)+Math.pow(a2,2)*(Math.pow(b1,2)+Math.pow(c1,2)-c1*d1+Math.pow(d1,2)-b1*(c1+d1))-(b1-c1)*(-b2*c1+b1*c2)*d2+(c1*(b2-2*c2)+b1*(-2*b2+c2))*d1*d2+(Math.pow(b1,2)-b1*c1+Math.pow(c1,2))*Math.pow(d2,2)+a1*(b2*(b1+c1)*c2-Math.pow(c2,2)*(b1+d1)-Math.pow(b2,2)*(c1+d1)+b2*(b1+d1)*d2+c2*(c1+d1)*d2-(b1+c1)*Math.pow(d2,2))+Math.pow(a1,2)*(Math.pow(b2,2)+Math.pow(c2,2)-c2*d2+Math.pow(d2,2)-b2*(c2+d2))+a2*(-b2*Math.pow(c1,2)+c1*c2*d1-b2*Math.pow(d1,2)-c2*Math.pow(d1,2)-Math.pow(c1,2)*d2+c1*d1*d2-Math.pow(b1,2)*(c2+d2)+b1*(c1*c2+b2*(c1+d1)+d1*d2)+a1*(-2*c1*c2+c2*d1+b2*(c1+d1)+c1*d2-2*d1*d2+b1*(-2*b2+c2+d2))))));
    const e2 = 1/24*(3*Math.pow(a1,2)+3*Math.pow(a2,2)+3*Math.pow(b1,2)-2*a2*b2+3*Math.pow(b2,2)-2*b1*c1+3*Math.pow(c1,2)-2*a2*c2-2*b2*c2+3*Math.pow(c2,2)-2*b1*d1-2*c1*d1+3*Math.pow(d1,2)-2*a1*(b1+c1+d1)-2*a2*d2-2*b2*d2-2*c2*d2+3*Math.pow(d2,2)+Math.sqrt((3*Math.pow(a1,2)+3*Math.pow(a2,2)+3*Math.pow(b1,2)+3*Math.pow(b2,2)-2*b1*c1+3*Math.pow(c1,2)-2*b2*c2+3*Math.pow(c2,2)-2*(b1+c1)*d1+3*Math.pow(d1,2)-2*a1*(b1+c1+d1)-2*(b2+c2)*d2+3*Math.pow(d2,2)-2*a2*(b2+c2+d2))**2-32*(Math.pow(b2,2)*Math.pow(c1,2)-2*b1*b2*c1*c2+Math.pow(b1,2)*Math.pow(c2,2)-Math.pow(b2,2)*c1*d1+b1*b2*c2*d1+b2*c1*c2*d1-b1*Math.pow(c2,2)*d1+Math.pow(b2,2)*Math.pow(d1,2)-b2*c2*Math.pow(d1,2)+Math.pow(c2,2)*Math.pow(d1,2)+Math.pow(a2,2)*(Math.pow(b1,2)+Math.pow(c1,2)-c1*d1+Math.pow(d1,2)-b1*(c1+d1))-(b1-c1)*(-b2*c1+b1*c2)*d2+(c1*(b2-2*c2)+b1*(-2*b2+c2))*d1*d2+(Math.pow(b1,2)-b1*c1+Math.pow(c1,2))*Math.pow(d2,2)+a1*(b2*(b1+c1)*c2-Math.pow(c2,2)*(b1+d1)-Math.pow(b2,2)*(c1+d1)+b2*(b1+d1)*d2+c2*(c1+d1)*d2-(b1+c1)*Math.pow(d2,2))+Math.pow(a1,2)*(Math.pow(b2,2)+Math.pow(c2,2)-c2*d2+Math.pow(d2,2)-b2*(c2+d2))+a2*(-b2*Math.pow(c1,2)+c1*c2*d1-b2*Math.pow(d1,2)-c2*Math.pow(d1,2)-Math.pow(c1,2)*d2+c1*d1*d2-Math.pow(b1,2)*(c2+d2)+b1*(c1*c2+b2*(c1+d1)+d1*d2)+a1*(-2*c1*c2+c2*d1+b2*(c1+d1)+c1*d2-2*d1*d2+b1*(-2*b2+c2+d2))))));    
    const m1 = -((-3*a1**2+3*a2**2-3*b1**2+3*b2**2-3*c1**2+3*c2**2+2*c1*d1-3*d1**2+2*b1*(c1+d1)+2*a1*(b1+c1+d1)-2*c2*d2+3*d2**2-2*b2*(c2+d2)-2*a2*(b2+c2+d2)+Math.sqrt(9*a1**4+9*a2**4+9*b1**4+18*b1**2*b2**2+9*b2**4-12*b1**3*c1-12*b1*b2**2*c1+22*b1**2*c1**2-14*b2**2*c1**2-12*b1*c1**3+9*c1**4-12*b1**2*b2*c2-12*b2**3*c2+72*b1*b2*c1*c2-12*b2*c1**2*c2-14*b1**2*c2**2+22*b2**2*c2**2-12*b1*c1*c2**2+18*c1**2*c2**2-12*b2*c2**3+9*c2**4-12*b1**3*d1-12*b1*b2**2*d1-4*b1**2*c1*d1+20*b2**2*c1*d1-4*b1*c1**2*d1-12*c1**3*d1-24*b1*b2*c2*d1-24*b2*c1*c2*d1+20*b1*c2**2*d1-12*c1*c2**2*d1+22*b1**2*d1**2-14*b2**2*d1**2-4*b1*c1*d1**2+22*c1**2*d1**2+20*b2*c2*d1**2-14*c2**2*d1**2-12*b1*d1**3-12*c1*d1**3+9*d1**4-12*a1**3*(b1+c1+d1)-4*(3*b2**3+b1**2*(3*b2-5*c2)+b2**2*c2+3*c2*(c1**2+c2**2-6*c1*d1+d1**2)+b2*(-5*c1**2+c2**2+6*c1*d1+3*d1**2)+6*b1*(b2*(c1-3*d1)+c2*(c1+d1)))*d2-2*(7*b1**2-11*b2**2-10*b1*c1+7*c1**2+2*b2*c2-11*c2**2+6*(b1+c1)*d1-9*d1**2)*d2**2-12*(b2+c2)*d2**3+9*d2**4-12*a2**3*(b2+c2+d2)+2*a2**2*(-7*b1**2+11*b2**2-7*c1**2+11*c2**2+10*c1*d1-7*d1**2+10*b1*(c1+d1)-2*c2*d2+11*d2**2-2*b2*(c2+d2))+2*a1**2*(9*a2**2+11*b1**2-7*b2**2+11*c1**2+10*b2*c2-7*c2**2-2*c1*d1+11*d1**2-2*b1*(c1+d1)+10*(b2+c2)*d2-7*d2**2-6*a2*(b2+c2+d2))-4*a2*(3*b2**3+3*c1**2*c2+3*c2**3+6*c1*c2*d1-5*c2*d1**2-5*c1**2*d2+c2**2*d2+6*c1*d1*d2+3*d1**2*d2+c2*d2**2+3*d2**3+b2**2*(c2+d2)+b1*(6*c1*c2-2*c2*d1+6*b2*(c1+d1)-2*c1*d2+6*d1*d2)+b2*(-5*c1**2+c2**2-2*c1*d1-5*d1**2-6*c2*d2+d2**2)+b1**2*(3*b2-5*(c2+d2)))-4*a1*(3*b1**3-5*b2**2*c1+3*c1**3+6*b2*c1*c2+3*c1*c2**2-5*b2**2*d1+c1**2*d1-2*b2*c2*d1-5*c2**2*d1+c1*d1**2+3*d1**3+b1**2*(c1+d1)+3*a2**2*(b1+c1+d1)-2*b2*c1*d2+6*c1*c2*d2+6*b2*d1*d2+6*c2*d1*d2-5*c1*d2**2+3*d1*d2**2+b1*(3*b2**2+c1**2-5*c2**2-6*c1*d1+d1**2-2*c2*d2-5*d2**2+6*b2*(c2+d2))+6*a2*(-3*c1*c2+c2*d1+b2*(c1+d1)+c1*d2-3*d1*d2+b1*(-3*b2+c2+d2)))))/(-2*(-3*b1*b2+b2*c1+b1*c2-3*c1*c2+b2*d1+c2*d1+a2*(b1+c1+d1)+(b1+c1-3*d1)*d2)+a1*(6*a2-2*(b2+c2+d2))));
    const m2 = -((3*a1**2-3*a2**2+3*b1**2-3*b2**2+3*c1**2-3*c2**2-2*c1*d1+3*d1**2-2*b1*(c1+d1)-2*a1*(b1+c1+d1)+2*c2*d2-3*d2**2+2*b2*(c2+d2)+2*a2*(b2+c2+d2)+Math.sqrt(9*a1**4+9*a2**4+9*b1**4+18*b1**2*b2**2+9*b2**4-12*b1**3*c1-12*b1*b2**2*c1+22*b1**2*c1**2-14*b2**2*c1**2-12*b1*c1**3+9*c1**4-12*b1**2*b2*c2-12*b2**3*c2+72*b1*b2*c1*c2-12*b2*c1**2*c2-14*b1**2*c2**2+22*b2**2*c2**2-12*b1*c1*c2**2+18*c1**2*c2**2-12*b2*c2**3+9*c2**4-12*b1**3*d1-12*b1*b2**2*d1-4*b1**2*c1*d1+20*b2**2*c1*d1-4*b1*c1**2*d1-12*c1**3*d1-24*b1*b2*c2*d1-24*b2*c1*c2*d1+20*b1*c2**2*d1-12*c1*c2**2*d1+22*b1**2*d1**2-14*b2**2*d1**2-4*b1*c1*d1**2+22*c1**2*d1**2+20*b2*c2*d1**2-14*c2**2*d1**2-12*b1*d1**3-12*c1*d1**3+9*d1**4-12*a1**3*(b1+c1+d1)-4*(3*b2**3+b1**2*(3*b2-5*c2)+b2**2*c2+3*c2*(c1**2+c2**2-6*c1*d1+d1**2)+b2*(-5*c1**2+c2**2+6*c1*d1+3*d1**2)+6*b1*(b2*(c1-3*d1)+c2*(c1+d1)))*d2-2*(7*b1**2-11*b2**2-10*b1*c1+7*c1**2+2*b2*c2-11*c2**2+6*(b1+c1)*d1-9*d1**2)*d2**2-12*(b2+c2)*d2**3+9*d2**4-12*a2**3*(b2+c2+d2)+2*a2**2*(-7*b1**2+11*b2**2-7*c1**2+11*c2**2+10*c1*d1-7*d1**2+10*b1*(c1+d1)-2*c2*d2+11*d2**2-2*b2*(c2+d2))+2*a1**2*(9*a2**2+11*b1**2-7*b2**2+11*c1**2+10*b2*c2-7*c2**2-2*c1*d1+11*d1**2-2*b1*(c1+d1)+10*(b2+c2)*d2-7*d2**2-6*a2*(b2+c2+d2))-4*a2*(3*b2**3+3*c1**2*c2+3*c2**3+6*c1*c2*d1-5*c2*d1**2-5*c1**2*d2+c2**2*d2+6*c1*d1*d2+3*d1**2*d2+c2*d2**2+3*d2**3+b2**2*(c2+d2)+b1*(6*c1*c2-2*c2*d1+6*b2*(c1+d1)-2*c1*d2+6*d1*d2)+b2*(-5*c1**2+c2**2-2*c1*d1-5*d1**2-6*c2*d2+d2**2)+b1**2*(3*b2-5*(c2+d2)))-4*a1*(3*b1**3-5*b2**2*c1+3*c1**3+6*b2*c1*c2+3*c1*c2**2-5*b2**2*d1+c1**2*d1-2*b2*c2*d1-5*c2**2*d1+c1*d1**2+3*d1**3+b1**2*(c1+d1)+3*a2**2*(b1+c1+d1)-2*b2*c1*d2+6*c1*c2*d2+6*b2*d1*d2+6*c2*d1*d2-5*c1*d2**2+3*d1*d2**2+b1*(3*b2**2+c1**2-5*c2**2-6*c1*d1+d1**2-2*c2*d2-5*d2**2+6*b2*(c2+d2))+6*a2*(-3*c1*c2+c2*d1+b2*(c1+d1)+c1*d2-3*d1*d2+b1*(-3*b2+c2+d2)))))/(2*(-3*b1*b2+b2*c1+b1*c2-3*c1*c2+b2*d1+c2*d1+a2*(b1+c1+d1)+(b1+c1-3*d1)*d2+a1*(-3*a2+b2+c2+d2))));
    var m = 0;
    if (e1 > e2) {m = 1/m1;} else {m = 1/m2;}
    b = my-mx*m;
    y = data2['y'];
    for (let i = 0; i < data2['x'].length; i++) {y[i] = m*data2['x'][i]+b}
    source2.change.emit();

    const data2c = source2c.data;
    data2c['x1'] = [a1,(a1+m*a2-b*m)/(1+m*m)]; data2c['y1'] = [a2,m*(a1+m*a2-b*m)/(1+m*m)+b];
    data2c['x2'] = [b1,(b1+m*b2-b*m)/(1+m*m)]; data2c['y2'] = [b2,m*(b1+m*b2-b*m)/(1+m*m)+b];
    data2c['x3'] = [c1,(c1+m*c2-b*m)/(1+m*m)]; data2c['y3'] = [c2,m*(c1+m*c2-b*m)/(1+m*m)+b];
    data2c['x4'] = [d1,(d1+m*d2-b*m)/(1+m*m)]; data2c['y4'] = [d2,m*(d1+m*d2-b*m)/(1+m*m)+b];
    source2c.change.emit();

    const data3 = source3.data;
    const angle = (180*Math.abs(Math.atan(m)-Math.atan(a))/(Math.PI)).toFixed(2);
    const text1 = ['Angle of intersection: ', angle.toString()].join('');
    const hyp1 = Math.hypot(data1c['x1'][0] - data1c['x1'][1], data1c['y1'][0] - data1c['y1'][1]);
    const hyp2 = Math.hypot(data1c['x2'][0] - data1c['x2'][1], data1c['y2'][0] - data1c['y2'][1]);
    const hyp3 = Math.hypot(data1c['x3'][0] - data1c['x3'][1], data1c['y3'][0] - data1c['y3'][1]);
    const hyp4 = Math.hypot(data1c['x4'][0] - data1c['x4'][1], data1c['y4'][0] - data1c['y4'][1]);
    const text2 = ['Sum of vertical distances: ', ((hyp1+hyp2+hyp3+hyp4).toFixed(2)).toString()].join('');
    const hypP1 = Math.hypot(data2c['x1'][0] - data2c['x1'][1], data2c['y1'][0] - data2c['y1'][1]);
    const hypP2 = Math.hypot(data2c['x2'][0] - data2c['x2'][1], data2c['y2'][0] - data2c['y2'][1]);
    const hypP3 = Math.hypot(data2c['x3'][0] - data2c['x3'][1], data2c['y3'][0] - data2c['y3'][1]);
    const hypP4 = Math.hypot(data2c['x4'][0] - data2c['x4'][1], data2c['y4'][0] - data2c['y4'][1]);
    const text3 = ['Sum of perpendicular distances: ', ((hypP1+hypP2+hypP3+hypP4).toFixed(2)).toString()].join('');
    data3['text'][0] = [text1, text2, text3].join('\\n');
    source3.change.emit();

""")

source.js_on_change('data', callback)
p.js_on_event('mousemove', callback)

draw_tool = PointDrawTool(renderers=[renderer], empty_value='red', num_objects=4)
p.add_tools(draw_tool)
p.toolbar.active_tap = draw_tool

show(column(p, table, sizing_mode="scale_width"))

for line in fileinput.input("lecture22-4points.html", inplace = 1): 
      print(line.replace("  <body>\n", "  <body style=\"margin:5%\">\n"), end='')